# Symbologies

In [1]:
import onetick.py as otp

You can query data using different symbologies.

In [32]:
trd = otp.DataSource('NYSE_TAQ', tick_type='TRD')
trd = trd[['PRICE','SIZE','EXCHANGE','COND']]
trd = trd.first(1)
merged = otp.merge([trd], symbols=['BTKR::::AAPL US','FGV::::btkr000BPH459'], identify_input_ts=True)
otp.run(merged, start=otp.dt(2022,3,1,10), end=otp.dt(2022,3,1,10,15), symbol_date=otp.dt(2022, 10, 1))

Time   PRICE  SIZE EXCHANGE  COND          SYMBOL_NAME TICK_TYPE
0 2022-03-01 10:00:00.003529175  165.75   100        Q  @         BTKR::::AAPL US       TRD
1 2022-03-01 10:00:00.003577531  298.53    50        Q  @  I  FGV::::BBG000BPH459       TRD

You can create a mapping between symbologies.

In [45]:
figi = otp.Symbols('NYSE_TAQ', symbology='FGV', show_original_symbols=True, for_tick_type='TRD')
figi, _ = figi[figi['SYMBOL_NAME']!='']
otp.run(figi, start=otp.dt(2022, 12, 1), end=otp.dt(2022, 12, 2))

Time   SYMBOL_NAME ORIGINAL_SYMBOL_NAME
0     2022-12-01  BBG000C2V3D6          NYSE_TAQ::A
1     2022-12-01  BBG00B3T3HD3         NYSE_TAQ::AA
2     2022-12-01  BBG01B0JRCS6        NYSE_TAQ::AAA
3     2022-12-01  BBG00LPXX872       NYSE_TAQ::AAAU
4     2022-12-01  BBG00YZC2Z91        NYSE_TAQ::AAC
...          ...           ...                  ...
11007 2022-12-01  BBG00YZ7S2J6      NYSE_TAQ::ZWRKW
11008 2022-12-01  BBG000H8R0N8        NYSE_TAQ::ZWS
11009 2022-12-01  BBG019XSYC89       NYSE_TAQ::ZYME
11010 2022-12-01  BBG007BBS8B7       NYSE_TAQ::ZYNE
11011 2022-12-01  BBG000BJBXZ2       NYSE_TAQ::ZYXI

[11012 rows x 3 columns]

In [46]:
btkr = otp.Symbols('NYSE_TAQ', symbology='BTKR', show_original_symbols=True, for_tick_type='TRD')
btkr, _ = btkr[btkr['SYMBOL_NAME']!='']
otp.run(btkr, start=otp.dt(2022, 12, 1), end=otp.dt(2022, 12, 2))

Time SYMBOL_NAME ORIGINAL_SYMBOL_NAME
0     2022-12-01        A US          NYSE_TAQ::A
1     2022-12-01       AA US         NYSE_TAQ::AA
2     2022-12-01      AAA US        NYSE_TAQ::AAA
3     2022-12-01     AAAU US       NYSE_TAQ::AAAU
4     2022-12-01      AAC US        NYSE_TAQ::AAC
...          ...         ...                  ...
10926 2022-12-01    ZWRKW US      NYSE_TAQ::ZWRKW
10927 2022-12-01      ZWS US        NYSE_TAQ::ZWS
10928 2022-12-01     ZYME US       NYSE_TAQ::ZYME
10929 2022-12-01     ZYNE US       NYSE_TAQ::ZYNE
10930 2022-12-01     ZYXI US       NYSE_TAQ::ZYXI

[10931 rows x 3 columns]

In [51]:
figi = otp.Symbols('NYSE_TAQ', symbology='FGV', show_original_symbols=True, for_tick_type='TRD')
btkr = otp.Symbols('NYSE_TAQ', symbology='BTKR', show_original_symbols=True, for_tick_type='TRD')
btkr, _ = btkr[btkr['SYMBOL_NAME']!='']
figi, _ = figi[figi['SYMBOL_NAME']!='']

mapping = otp.functions.join(figi, btkr, on=btkr['ORIGINAL_SYMBOL_NAME']==figi['ORIGINAL_SYMBOL_NAME'], how="inner")

mapping  = mapping.rename({'RIGHT_SYMBOL_NAME'   : 'BTKR',
                           'SYMBOL_NAME'         : 'FIGI',
                           'ORIGINAL_SYMBOL_NAME': 'DB_SYMBOL'})

mapping = mapping[['FIGI', 'BTKR', 'DB_SYMBOL']]

otp.run(mapping, start=otp.dt(2022, 12, 1), end=otp.dt(2022, 12, 2))

Time          FIGI      BTKR        DB_SYMBOL
0     2022-12-01  BBG000C2V3D6      A US      NYSE_TAQ::A
1     2022-12-01  BBG00B3T3HD3     AA US     NYSE_TAQ::AA
2     2022-12-01  BBG01B0JRCS6    AAA US    NYSE_TAQ::AAA
3     2022-12-01  BBG00LPXX872   AAAU US   NYSE_TAQ::AAAU
4     2022-12-01  BBG00YZC2Z91    AAC US    NYSE_TAQ::AAC
...          ...           ...       ...              ...
11005 2022-12-01  BBG00YZ7S2J6  ZWRKW US  NYSE_TAQ::ZWRKW
11006 2022-12-01  BBG000H8R0N8    ZWS US    NYSE_TAQ::ZWS
11007 2022-12-01  BBG019XSYC89   ZYME US   NYSE_TAQ::ZYME
11008 2022-12-01  BBG007BBS8B7   ZYNE US   NYSE_TAQ::ZYNE
11009 2022-12-01  BBG000BJBXZ2   ZYXI US   NYSE_TAQ::ZYXI

[11010 rows x 4 columns]

And here is an example for a non-US market

In [52]:
# 'FGV' is venue FIGI
# 'FGC' is composite FIGI
fgv = otp.Symbols('LSE', symbology='FGV', show_original_symbols=True, for_tick_type='TRD')
tkr = otp.Symbols('LSE', symbology='TKR', show_original_symbols=True, for_tick_type='TRD')

mapping = otp.functions.join(fgv, tkr, on=fgv['ORIGINAL_SYMBOL_NAME']==tkr['ORIGINAL_SYMBOL_NAME'], how="inner")

mapping, _ = mapping[mapping['SYMBOL_NAME'] != '']
mapping  = mapping.rename({'RIGHT_SYMBOL_NAME'   : 'TICKER',
                           'SYMBOL_NAME'         : 'FIGI',
                           'ORIGINAL_SYMBOL_NAME': 'DB_SYMBOL'})

mapping = mapping[['TICKER', 'FIGI', 'DB_SYMBOL']]
start = otp.dt(2022, 5, 20)
end = otp.dt(2022, 5, 25)

otp.run(mapping, start=otp.dt(2022, 12, 1), end=otp.dt(2022, 12, 2))

Time TICKER          FIGI  DB_SYMBOL
0    2022-12-01   020Y  BBG007XBDG85  LSE::020Y
1    2022-12-01   0A05  BBG00SYG7Q00  LSE::0A05
2    2022-12-01   0A07  BBG00NWMW214  LSE::0A07
3    2022-12-01   0A08  BBG00NWMVL13  LSE::0A08
4    2022-12-01   0A0B  BBG00NWMW143  LSE::0A0B
...         ...    ...           ...        ...
5332 2022-12-01   ZNWD  BBG00JG082G0  LSE::ZNWD
5333 2022-12-01    ZOO  BBG000DBR279   LSE::ZOO
5334 2022-12-01   ZPHR  BBG000DB8YK5  LSE::ZPHR
5335 2022-12-01    ZTF  BBG000BGXLF2   LSE::ZTF
5336 2022-12-01    ZYT  BBG000BZPV76   LSE::ZYT

[5337 rows x 4 columns]

# Symbol name changes
Symbol name changes are easy to handle with the `symbol_date` parameter of `otp.run()` which provides the "as of" date for the symbols. For example, you can pass `META` while setting `symbol_date` to any date after 2022-06-09 or `FB` and `symbol_date` before 2022-06-09.

In [53]:
trd = otp.DataSource('NYSE_TAQ', tick_type='TRD')
trd = trd.first(5)
otp.run(trd, start=otp.dt(2023,2,2), end=otp.dt(2023,2,3), symbols='META', symbol_date=otp.dt(2023,2,2))

Time EXCHANGE  COND STOP_STOCK SOURCE TRF TTE TICKER   PRICE DELETED_TIME  TICK_STATUS  SIZE  CORR  SEQ_NUM TRADE_ID              PARTICIPANT_TIME                      TRF_TIME  OMDSEQ
0 2023-02-02 00:00:00.100474511        Q  @ TI                 N       0   META  183.13   1970-01-01            0    10     0  7286117   160978 2023-02-02 00:00:00.100458331 1970-01-01 00:00:00.000000000       0
1 2023-02-02 00:00:00.825173183        Q  @FT                  N       1   META  183.13   1970-01-01            0   100     0  7286118   160979 2023-02-02 00:00:00.825157012 1970-01-01 00:00:00.000000000       0
2 2023-02-02 00:00:00.835111354        K  @ TI                 N       1   META  183.18   1970-01-01            0     2     0  7286119    54129 2023-02-02 00:00:00.834865000 1970-01-01 00:00:00.000000000       0
3 2023-02-02 00:00:00.837461982        Q  @ TI                 N       0   META  183.18   1970-01-01            0     5     0  7286123   160980 2023-02-02 00:00:00.837446438 1970-01-01 00:00:00.000000000       0
4 2023-02-02 00:00:00.877120054        D  @ TI                 N   Q   0   META  183.13   1970-01-01            0    13     0  7286124   117854 2023-02-02 00:00:00.875000000 2023-02-02 00:00:00.877093881       0

In [54]:
trd = otp.DataSource('NYSE_TAQ', tick_type='TRD')
trd = trd.first(5)
otp.run(trd, start=otp.dt(2023,2,2), end=otp.dt(2023,2,3), symbols='FB', symbol_date=otp.dt(2021,2,2))

Time EXCHANGE  COND STOP_STOCK SOURCE TRF TTE TICKER   PRICE DELETED_TIME  TICK_STATUS  SIZE  CORR  SEQ_NUM TRADE_ID              PARTICIPANT_TIME                      TRF_TIME  OMDSEQ
0 2023-02-02 00:00:00.100474511        Q  @ TI                 N       0   META  183.13   1970-01-01            0    10     0  7286117   160978 2023-02-02 00:00:00.100458331 1970-01-01 00:00:00.000000000       0
1 2023-02-02 00:00:00.825173183        Q  @FT                  N       1   META  183.13   1970-01-01            0   100     0  7286118   160979 2023-02-02 00:00:00.825157012 1970-01-01 00:00:00.000000000       0
2 2023-02-02 00:00:00.835111354        K  @ TI                 N       1   META  183.18   1970-01-01            0     2     0  7286119    54129 2023-02-02 00:00:00.834865000 1970-01-01 00:00:00.000000000       0
3 2023-02-02 00:00:00.837461982        Q  @ TI                 N       0   META  183.18   1970-01-01            0     5     0  7286123   160980 2023-02-02 00:00:00.837446438 1970-01-01 00:00:00.000000000       0
4 2023-02-02 00:00:00.877120054        D  @ TI                 N   Q   0   META  183.13   1970-01-01            0    13     0  7286124   117854 2023-02-02 00:00:00.875000000 2023-02-02 00:00:00.877093881       0